# Rumintegraler

Demo af Christian Mikkelstrup og Hans Henrik Hermansen

In [ ]:
from sympy import *
from dtumathtools import * 
init_printing()

## Rumligt område begrænset af graf-flade
Givet funktionen 
$$
f(x,y,z) = (1-x) ^ 2
$$
skal vi finde rumintegralet af $f$ over det *tetraeder* $T$, som er udspændt af punkterne $(0,0,0), (1,0,0), (0,1,0)$ og $(0,0,1)$.


In [ ]:
## Tænk ikke for meget over dette

x,y,z,u,v,w = symbols("x y z u v w",real=True)
ur = (u,0,1)
l1 = dtuplot.plot3d_parametric_line(u,0,0,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
l2 = dtuplot.plot3d_parametric_line(0,u,0,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
l3 = dtuplot.plot3d_parametric_line(0,0,u,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
l4 = dtuplot.plot3d_parametric_line(1-u,u,0,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
l5 = dtuplot.plot3d_parametric_line(u,0,1-u,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
l6 = dtuplot.plot3d_parametric_line(0,u,1-u,ur,show=False,use_cm=False,rendering_kw={"color":"red"})
grundflade = dtuplot.plot3d_parametric_surface(u * (1-v),v,0,ur,(v,0,1),show=False,rendering_kw={"color":"blue","alpha":0.75})
dash1 = dtuplot.plot3d_parametric_line(0.3,0.7*u,0,ur,show=False,use_cm=False,rendering_kw={"color":"grey","linestyle":"dashed"})
dash2 = dtuplot.plot3d_parametric_line(0.3,0.7-0.7*u,0.7*u,ur,show=False,use_cm=False,rendering_kw={"color":"grey","linestyle":"dashed"})
dash3 = dtuplot.plot3d_parametric_line(0.3,0,0.7*u,ur,show=False,use_cm=False,rendering_kw={"color":"grey","linestyle":"dashed"})
pil3d = dtuplot.quiver(Matrix([0.3,0.375,0]),Matrix([0,0,0.375]),show=False,rendering_kw={"color":"black"})

bund = dtuplot.plot_implicit((x >= 0) & (x <= 1) & (y >= 0) & (y <= 1-x),(x,0,1),(y,0,1),show=False)
pil2d = dtuplot.quiver(Matrix([0.2,0]),Matrix([0,0.8]),show=False,rendering_kw={"color":"black","width":0.025})

skelet = (l1 + l2 + l3 + l4 + l5 + l6 + dash1 + dash2 + dash3 + pil3d)
tetra = grundflade + skelet
tetra.legend=False
tetra.camera={"azim":25,"elev":25}
tetra.size=(6,6)
trekant = bund + pil2d
trekant.legend=False
trekant.grid=False

d = dtuplot.plotgrid(tetra,trekant, nr = 1, nc = 2,size=(6,6))

Bunden af $T$ er vist som den blå trekant, mens toppen beskrevet som grafen til funktionen $h(x,y) = 1 - x - y$.

Vi parametriserer den blå trekant som sædvanlig vis, så et punkt på den blå trekant er beskrevet af
$$
\begin{bmatrix} x \\ y \end{bmatrix} = \begin{bmatrix} u \\ v (u-1) \end{bmatrix}, \quad u \in [0,1], \, v \in [0,1]
$$
I punktet $(u,v(u-1))$ har $h$ værdiern $z = h(u,v(u-1)) = 1 - u - v(u-1)$. Så nu vil vi gerne parametrisere det generelle linjestykke mellem et punkt $(u,v(u-1),0)$ og $(u,v(u-1),1-u-v(u-1))$. Dette resulterer i følgende parameterfremstilling:

In [ ]:
f = (1-x) ** 2
h = 1 - x - y
bund_punkt = Matrix([u,v*(1-u),0])
top_punkt = Matrix([u,v*(1-u),h.subs({x:u,y:v*(1-u)})])
r = bund_punkt + w * (top_punkt - bund_punkt)
r

hvor $u \in [0,1]$, $v \in [0,1]$ og $w \in [0,1]$. Lad os finde den Jacobi-funktion, der indgår i rumintegralet. Først udregnes Jacobi-matricen og derefter determinanten af denne:

In [ ]:
Matrix.hstack(*[r.diff(v) for v in [u,v,w]])

In [ ]:
determinanten = _.det()   # underscore holder værdien fra seneste output
Jacobi = determinanten
# vi ved at determinanten er positiv i det betragtede område, så det er ikke nødvendigt at tage absolut værdien
# Jacobi.simplify() 
Jacobi.factor()


Nu finder vi rumintegralet som det tredobbelte intregral:
$$
\int_T f(x,y,z) \, \mathrm{d}\mu = \int_0^1 \int_0^1 \int_0^1 f(r(u,v,w)) Jacobi \, \mathrm{d}u\mathrm{d}v\mathrm{d}w
$$

In [ ]:
M = integrate(f.subs({x:r[0],y:r[1],z:r[2]}) * Jacobi, (u,0,1), (v,0,1), (w,0,1))
M

### Fortolkning: Masse og Massemidtpunkt

Hvis vi fortolker $f$ som en massetæthedsfunktion, har tetraederet altså massen $M=\frac{1}{10}$.
Massemidtpunktets koordinater kan bestemmes ud fra formlen:
$$
\xi = \frac{1}{M} \begin{bmatrix} \int_T x f(x,y,z) \, \mathrm{d}\mu \\ \int_T y f(x,y,z) \, \mathrm{d}\mu \\ \int_T z f(x,y,z) \, \mathrm{d}\mu \end{bmatrix}
$$


In [ ]:
xi = Matrix([integrate(coord * f.subs({x:r[0],y:r[1],z:r[2]})*Jacobi,(u,0,1),(v,0,1),(w,0,1)) for coord in r])/M
xi

## Omdrejningslegeme
Et profilområde ligger i $(x,z)$-planen ligger mellem hyperblen $z=\frac{1}{x}$ og $x$-aksen for $x \in [\frac{1}{2},2]$:

In [ ]:
dtuplot.plot_implicit((x >= 1/2) & (x <= 2) & (y <= 1/x) & (y >= 0),(x,0,2),(y,0,2))

Området parametriseres som:


In [ ]:
profil = Matrix([u,0,v/u])
profil

hvor $u \in [\frac{1}{2},2]$ og $v \in [0,1]$. For at finde parameterfremstillingen for omdrejnignslegemet ganger vi profil-områdets parameterfremstilling med rotationsmatricen:

In [ ]:
legeme = Matrix([[cos(w),-sin(w),0],[sin(w),cos(w),0],[0,0,1]]) * profil
legeme

Lad os nu finde den tilhørende Jacobi-funktion:

In [ ]:
determinanten = Matrix.hstack(*[legeme.diff(v) for v in [u,v,w]]).det()
Jacobi = abs(determinanten.simplify())
Jacobi

I dette tilfælde er Jacobi-funktionen enormt simpel. Vi kan nu udregne rumfanget af omdrejningslegemet:
$$
\int_{\omega}f(x,y,z) \, \mathrm{d}\mu = \int_0^{2\pi} \int_0^1 \int_{\frac{1}{2}} ^ 2 f(r(u,v,w)) Jacobi \, \mathrm{d}u\mathrm{d}v\mathrm{d}w
$$

In [ ]:
integrate(Jacobi,(u,S(1)/2,2),(v,0,1),(w,0,2*pi))

## Cylinderlegeme
En mur er rejst mellem de to ledekurver:

In [ ]:
l1 = Eq(y,cos(x))
l2 = Eq(y,cos(x)+1)
x_range = (x,0,2*pi)

dtuplot.plot_implicit(l1,l2,x_range,(y,-1,2),aspect="equal")

Murens højde er variabel idet $z \in [0,\frac{x}{2}]$. En parameterfremstilling for muren er:

In [ ]:
mur = Matrix([u,cos(u)+v,w*u/2])
mur

hvor $u \in [0,2\pi]$, $v \in [0,1]$ og $w \in [0,1]$

In [ ]:
determinanten = Matrix.hstack(*[mur.diff(v) for v in [u,v,w]]).det()
## antag at variablerne er positive
Jacobi = abs(posify(determinanten)[0])
Jacobi


Betragt funktionen 
$$
f(x,y,z) = \frac{1}{x}
$$
Vi kan nu udregne dette tredobbelt integral:
$$
\int_T f(x,y,z) \, \mathrm{d} \mu = \int_0^1 \int_0^1 \int_0^{2\pi} f(r(u,v,w))Jacobi \, \mathrm{d}u\mathrm{d}v\mathrm{d}w
$$

In [ ]:
f = 1/x
integrand = (f.subs({x:mur[0],y:mur[1],z:mur[2]}) * Jacobi).simplify()
integrand

In [ ]:
integrand = S(1)/2
integrate(integrand,(u,0,2*pi),(v,0,1),(w,0,1))
